In [1]:
import numpy as np
import itertools, copy
import os

In [2]:
# a function, generate all (possible) non-increasing outdegree sequences for simple graphs
# p, number of vertices of the graphs
# edges, number of edges of the graphs
def out_degree_seqs(p, edges):
    seqlist = []
    
    for k in reversed(range(1,p)):

        stack = [(1, [k], k)]
        
        while stack:
            
            cur, seq, csum = stack.pop()
            if cur <= p:
                if csum == edges:
                    #seqlist.append(seq[:])
                    seqlist.append(seq + [0]*(p-cur))
                else:
                    for i in range(1,min(edges-csum, seq[-1], p-cur+1)+1):
                        csum += i
                        stack.append((cur+1, seq+[i], csum))
                        csum -= i
    return seqlist


# a function, output all graphs for a specific outdegree sequence
# p, the number of vertices of the graphs
# seq, the out degree sequence of the graphs
def gen_graphs(p, seq):
    assert len(seq) == p
    
    # generate all graphs corresponding to a specific outdegree sequence, with tail nodes representation
    adj = np.array([[0 for i in range(p)] for j in range(p)])
    stack = [(0, [], adj)]
    tmp = []
    
    while stack:
        cur, path, adj = stack.pop() #matrix B, i,j entry is j->i
        if cur == p:
            tmp.append(path)
        else:
            if seq[cur] == 0:
                tmp.append(path + [set()] * (p-cur-1))
            else:
                for ch in list(itertools.combinations([x for x in range(p) if x != cur], seq[cur])): # all possible children set of size seq[cur]
                    ch = list(ch)
                    
                    if sum(adj[ch, cur]) == 0 and sum(adj[cur, ch]) == 0: # no edge from ch(cur) to cur(ch), ch can be children set of cur
                        adj[ch, cur] = 1
                        stack.append((cur+1, path+[ch], copy.deepcopy(adj)))
                        adj[ch, cur] = 0 # *cur to children, reset to 0
                        
                    
    # transform to edge representation
    def trans(path):
        res = []
        for i, item in enumerate(path):
            if item:
                res.extend(list(map(lambda x: (i,x), item)))
        return res
    
    #return tmp
    return list(map(trans, tmp))


# a function, output all cyclic graphs for a specific outdegree sequence
# p, the number of vertices of the graphs
# seq, the out degree sequence of the graphs
def gen_cyclic_graphs(p, seq):

    graph_list = gen_graphs(p, seq)

    return [G for G in graph_list if not DiGraph(G).is_directed_acyclic()]

In [3]:
# a function, output all parentally closed sets of a graph G with respect to a node i
def parentally_closed_sets(G, i):

    ne = G.neighbors(i)

    pa_cl_sets = []
    
    for L in subsets(ne):

        paL = sorted(set(flatten([G.neighbors_in(l) for l in L])))
        
        intersection = [l for l in paL if l in ne]
        
        if all([l in L for l in intersection]):

            pa_cl_sets.append(L)

    return pa_cl_sets[1:]
    

# a function, searches through all parentally closed sets of graphs G_1 and G_2 and attempts to find a set
# which can be used to distinguish them in the sense of Theorem 4.11
# If it finds such a set it outputs a list [True, i, L, # ch_1(i) \cap L, # ch_2(i) \cap L] such that 
# L is a parentally closed set in G_k with respect to node i and #ch_k(i) \cap L > # ch_(3-k)(i) \cap L
# If it finds no such set, then it ouputs [False]
def pc_distinguish(G1, G2):

    V = sorted(set(G1.vertices()))

    for i in V:

        pcs1 = map(set, parentally_closed_sets(G1, i))

        for L in pcs1:

            if len(L.intersection(G1.neighbors_out(i))) > len(L.intersection(G2.neighbors_out(i))):

                return [True, i, L, len(L.intersection(G1.neighbors_out(i))), len(L.intersection(G2.neighbors_out(i)))]


    for i in V:

        pcs2 = map(set, parentally_closed_sets(G2, i))

        for L in pcs2:

            if len(L.intersection(G2.neighbors_out(i))) > len(L.intersection(G1.neighbors_out(i))):

                return [True, i, L, len(L.intersection(G1.neighbors_out(i))), len(L.intersection(G2.neighbors_out(i)))]


    return [False]

In [4]:
# This prints a list of all possible out degree sequences for 4 node graphs grouped by the number of edges
p = 6

certs = []

for e in range(1, binomial(p,2)):

    for seq in out_degree_seqs(p, e):

        print(seq)

    print()

[1, 0, 0, 0, 0, 0]

[2, 0, 0, 0, 0, 0]
[1, 1, 0, 0, 0, 0]

[3, 0, 0, 0, 0, 0]
[2, 1, 0, 0, 0, 0]
[1, 1, 1, 0, 0, 0]

[4, 0, 0, 0, 0, 0]
[3, 1, 0, 0, 0, 0]
[2, 2, 0, 0, 0, 0]
[2, 1, 1, 0, 0, 0]
[1, 1, 1, 1, 0, 0]

[5, 0, 0, 0, 0, 0]
[4, 1, 0, 0, 0, 0]
[3, 2, 0, 0, 0, 0]
[3, 1, 1, 0, 0, 0]
[2, 2, 1, 0, 0, 0]
[2, 1, 1, 1, 0, 0]
[1, 1, 1, 1, 1, 0]

[5, 1, 0, 0, 0, 0]
[4, 2, 0, 0, 0, 0]
[4, 1, 1, 0, 0, 0]
[3, 3, 0, 0, 0, 0]
[3, 2, 1, 0, 0, 0]
[3, 1, 1, 1, 0, 0]
[2, 2, 2, 0, 0, 0]
[2, 2, 1, 1, 0, 0]
[2, 1, 1, 1, 1, 0]
[1, 1, 1, 1, 1, 1]

[5, 2, 0, 0, 0, 0]
[5, 1, 1, 0, 0, 0]
[4, 3, 0, 0, 0, 0]
[4, 2, 1, 0, 0, 0]
[4, 1, 1, 1, 0, 0]
[3, 3, 1, 0, 0, 0]
[3, 2, 2, 0, 0, 0]
[3, 2, 1, 1, 0, 0]
[3, 1, 1, 1, 1, 0]
[2, 2, 2, 1, 0, 0]
[2, 2, 1, 1, 1, 0]
[2, 1, 1, 1, 1, 1]

[5, 3, 0, 0, 0, 0]
[5, 2, 1, 0, 0, 0]
[5, 1, 1, 1, 0, 0]
[4, 4, 0, 0, 0, 0]
[4, 3, 1, 0, 0, 0]
[4, 2, 2, 0, 0, 0]
[4, 2, 1, 1, 0, 0]
[4, 1, 1, 1, 1, 0]
[3, 3, 2, 0, 0, 0]
[3, 3, 1, 1, 0, 0]
[3, 2, 2, 1, 0, 0]
[3, 2, 1, 1, 1, 0]
[3, 1

In [42]:
# This block of code takes about 60 minutes to run and will recreate entirely new certificate files
# in the same directory that this notebook is in
# only rerun this if you wish to try new random samples
p = 6
certs = []

# This loops over all possible numbers of edges for a graph with p vertices
# For the purposes of identifiability we only need to compare graphs with the same number of edges
for e in range(1, binomial(p,2)):

    # This loops over all possible outdegree sequences for a graph with e edges
    # By our Outdegree Theorem we know we only need to check graphs with the same outdegree sequence
    for seq in out_degree_seqs(p, e):

        certs_for_seq = []

        # This creates all possible cyclic graphs since by Theorem 5.2 we know we only need to check pairs
        # where both graphs are cyclic
        graph_list = gen_cyclic_graphs(p, seq)

        if len(graph_list) < 2:
            
            continue

        strongly_conn_comps = [sorted([sorted(c) for c in DiGraph(G).strongly_connected_components()]) for G in graph_list]

        unique_comps = []

        for c in strongly_conn_comps:

            if not c in unique_comps:

                unique_comps.append(c)
            else:
                continue

        if len(unique_comps) < 2:
            
            continue
        
        # This loops over all possible pairs of the cyclic graphs if there are less than 100,000
        # If there are more than 100,000 it samples 100,000 random pairs
        # We then apply pc_distinguish to find a parentally closed set which satisfies the hypotheses of Theorem 4.11
        if binomial(len(graph_list), 2) <= 100000:
        
            for S in Subsets(range(len(graph_list)), 2):
    
                G1 = DiGraph(graph_list[S[0]])
                G2 = DiGraph(graph_list[S[1]])
                
                certs_for_seq.append([S, pc_distinguish(G1, G2)])
        
        else:
            trials = 100000
            
            while trials > 0:

                S = Subsets(range(len(graph_list)), 2).random_element()
                G1 = DiGraph(graph_list[S[0]])
                G2 = DiGraph(graph_list[S[1]])
                C1 = sorted([sorted(c) for c in G1.strongly_connected_components()])
                C2 = sorted([sorted(c) for c in G2.strongly_connected_components()])
                
                if C1 == C2:

                    continue

                else:
                    certs_for_seq.append([S, pc_distinguish(G1, G2)])
                    trials -= 1

        # This saves the certificates as a sage object so they may be easily verified again
        save(certs_for_seq, 'certs' + ''.join([str(i) for i in seq]))

In [5]:
# This block of code verifies all of the certificates we have already found are true
outcomes_by_seq = []

# this loops through all possible numbers of edges e
for e in range(1, binomial(p,2)):

    # this loops over all possible out-degree sequence which sum to e
    for seq in out_degree_seqs(p, e):

        graph_list = gen_cyclic_graphs(p, seq)
        
        if len(graph_list) < 2:

            continue

        strongly_conn_comps = [sorted([sorted(c) for c in DiGraph(G).strongly_connected_components()]) for G in graph_list]
        
        unique_comps = []

        for c in strongly_conn_comps:

            if not c in unique_comps:

                unique_comps.append(c)
            else:
                continue

        if len(unique_comps) < 2:
            
            continue

        if len(unique_comps) < 2:
            
            continue
            
        certs = load('Certificates/' + 'certs' + ''.join([str(i) for i in seq]))

        # This extracts the boolean which records whether or not pc_distinguish succeeded for that pair of graphs
        # It then checks that in all 100,000 cases the method succeeded
        
        
        
# This checks that for each outdegree sequence, pc_distinguish succeeded in distinguishing all pairs
verify_all_certs = all(outcomes_by_seq)

verify_all_certs

True